In [56]:
import geopandas as gpd
import pandas as pd
import folium as fl
import shapely

In [159]:
bureaux = pd.read_csv(
    'table-bv-reu.csv',
    dtype={
        'id_brut_reu': str,
        'id_brut_insee': str,
        'code_commune': str,
        'code': str,
        'libelle_reu': str,
        'num_voie_reu': str,
        'voie_reu': str,
        'cp_reu': str,
        'commune_reu': str,
        'nb_adresses_initial': str,
        'nb_adresses_final': str,
        'id_brut_miom': str
    })

In [195]:
addrs = []
def getAddresses():
    for i, r in bureaux.iterrows():
        curr_addr = r['num_voie_reu'] + ' ' + r['voie_reu']
        if type(r['commune_reu']) == str:
            curr_addr += ', ' + r['commune_reu']
        addrs.append(curr_addr)
getAddresses()
print(len(addrs))

68839


In [196]:
for curr in addrs:
    if type(curr) == str:
        print(curr)

  Salle des fêtes, abergement clemenciat
1 Place de la Mairie, l abergement de varey
  AVENUE LEON BLUM, amberieu en bugey
  AVENUE LEON BLUM, amberieu en bugey
  RUE DES ARENES, amberieu en bugey
  AVENUE LEON BLUM, amberieu en bugey
  AVENUE LEON BLUM, amberieu en bugey
  RUE VICTOR HUGO, amberieu en bugey
  RUE JACQUES PREVERT, amberieu en bugey
  RUE JACQUES PREVERT, amberieu en bugey
  MAIRIE, amberieux en dombes
507 Grande rue, ambleon
   , ambronay
   , ambronay
8  IMPASSE LES CORREES, ambutrix
  La Mairie, andert et condon
230  Rue de la Mairie, anglefort
20 rue de la Fruitière, apremont
50 Place de la mairie, aranc
239  rue de la Mairie, arandas
1415 avenue Général Andréa, arbent
1415 avenue Général Andréa, arbent
   , arboys en bugey
   , arboys en bugey
388  CHEMIN DU ROSET, arbigny
  Salle des Sociétés, argis
  MAIRIE ARMIX, armix
  Mairie - 363 rue J-M Vianney, ars sur formans
  RUE DES GLIERES, artemare
23 ROUTE DU PORT, asnieres sur saone
95  rue de l'église, attignat
95

In [227]:
from geopy.geocoders import Nominatim
import sys

locations = []
def replaceAddressesWithCoordinates():
    loc = Nominatim(user_agent="Geopy Library")

    for i in range(len(addrs)):
        prompt = str(i / len(addrs) * 100) + '%'
        prompt += ' ' + str(i) + '/' + str(len(addrs))
        sys.stdout.write('\r' + prompt)
        if type(addrs[i]) == str:
            try:
                locFound = loc.geocode(addrs[i])
                if locFound != None:
                    locations.append(locFound)
                    del addrs[i]
            except Exception as e:
                prompt = ''

replaceAddressesWithCoordinates()

1.6711429424052522% 1120/67020

KeyboardInterrupt: 

In [ ]:
for curr in addrs:
    if type(curr) == str:
        print(curr)

In [ ]:
geojson = gpd.read_file('./bureaux-de-votes.geojson')

In [52]:
m = fl.Map(location=[46.603354, 1.888334], zoom_start=5, prefer_canvas=True)

In [53]:
geojson

id_bv num_bv                                       geo_point_2d  \
0    13-12    012  {'lon': 2.367434603574184, 'lat': 48.829783705...   
1      1-1    001  {'lon': 2.341064487067419, 'lat': 48.860083526...   
2      1-6    006  {'lon': 2.3483838366633822, 'lat': 48.86258867...   
3     3-10    010  {'lon': 2.3551721154803693, 'lat': 48.86362013...   
4      8-4    004  {'lon': 2.316406689843671, 'lat': 48.879313359...   
..     ...    ...                                                ...   
894  20-25    025  {'lon': 2.403113236156781, 'lat': 48.867556143...   
895  17-21    021  {'lon': 2.324907367489849, 'lat': 48.896478980...   
896  17-68    068  {'lon': 2.3129044150118303, 'lat': 48.89006792...   
897  17-52    052  {'lon': 2.3030106054596278, 'lat': 48.88603404...   
898  17-44    044  {'lon': 2.3037493778451874, 'lat': 48.88075294...   

                                 lib                         adresse     cp  \
0                ECOLE ELEMENTAIRE A           33 PLACE JEANNE D ARC  75013   
1    EX-MAIRIE DU 1ER ARRONDISSEMENT               4 PLACE DU LOUVRE  75001   
2     CONSERVATOIRE MUNICIPAL MOZART         7 PASSAGE DE LA CANOPEE  75001   
3                   ECOLE MATERNELLE                   25 RUE CHAPON  75003   
4              LYCEE RACINE - ANNEXE                38 RUE DE NAPLES  75008   
..                               ...                             ...    ...   
894                 ECOLE MATERNELLE               12 RUE BRETONNEAU  75020   
895                ECOLE ELEMENTAIRE           1 RUE JACQUES KELLNER  75017   
896                ECOLE ELEMENTAIRE  34 RUE  MSTISLAV ROSTROPOVITCH  75017   
897    ECOLE MATERNELLE GUSTAVE DORE          2 RUE CHARLES GERHARDT  75017   
898     ECOLE HOTELIERE JEAN DROUANT                  20 RUE MEDERIC  75017   

                     geometry  
0    POINT (2.36743 48.82978)  
1    POINT (2.34106 48.86008)  
2    POINT (2.34838 48.86259)  
3    POINT (2.35517 48.86362)  
4    POINT (2.31641 48.87931)  
..                        ...  
894  POINT (2.40311 48.86756)  
895  POINT (2.32491 48.89648)  
896  POINT (2.31290 48.89007)  
897  POINT (2.30301 48.88603)  
898  POINT (2.30375 48.88075)  

[899 rows x 7 columns]

In [54]:
for _, r in geojson.iterrows():
    fl.GeoJson(
        r['geometry'],
        marker=fl.Circle(radius=4, fill_color="orange", fill_opacity=0.4, color="black", weight=1),
    ).add_to(m)

In [55]:
m